In [1]:
import numpy as np
import pandas as pd
from sklearn.linear_model import LinearRegression
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
import optuna
from optuna.samplers import TPESampler
from sklearn.metrics import r2_score, mean_squared_error, mean_absolute_error

from plotly.io import show

In [3]:
# データの読み込み
data = pd.read_excel('data.xlsx', header = 1)

# 特徴量とターゲットの分離
X = data[['Concentration', 'time']]
y_Fe = data['Fe']
y_Al = data['Al']
y_Mn = data['Mn']

In [4]:
# 目的関数の定義 (MLR 用)
def objective_mlr(trial):
    # MLR モデルの定義
    model = LinearRegression()

    # 試行による最適化パラメータ
    X_train = pd.DataFrame({
        'Concentration': [trial.suggest_float('Concentration', 1.0, 3.0)],
        'time': [trial.suggest_float('time', 2.0, 60.0)]
    })
    
    # モデルのトレーニング
    model.fit(X, y_Fe)

    # 予測
    y_pred_Fe = model.predict(X_train)
    y_pred_Al = model.predict(X_train)
    y_pred_Mn = model.predict(X_train)

    # 目的関数の計算（Fe の最大化、Al の最小化、Mn の安定化）
    return -((y_pred_Fe[0] - y_pred_Al[0]) - abs(y_pred_Mn[0] - 5.3))

In [5]:
# Optunaによる最適化 (MLR)
study_mlr = optuna.create_study(direction='minimize', sampler=TPESampler())
study_mlr.optimize(objective_mlr, n_trials=500)

# 最適解の表示
print(f"MLR 最適解: {study_mlr.best_params}")

[I 2024-09-07 18:40:57,163] A new study created in memory with name: no-name-604f7356-7f9d-4436-9d26-7bb59a5afb7a
[I 2024-09-07 18:40:57,170] Trial 0 finished with value: 5.144920945090615 and parameters: {'Concentration': 2.6914668566911235, 'time': 18.02543767051039}. Best is trial 0 with value: 5.144920945090615.
[I 2024-09-07 18:40:57,176] Trial 1 finished with value: 5.11964857237937 and parameters: {'Concentration': 2.051406538079611, 'time': 49.67693688573273}. Best is trial 1 with value: 5.11964857237937.
[I 2024-09-07 18:40:57,182] Trial 2 finished with value: 5.126950501691151 and parameters: {'Concentration': 2.290095265495954, 'time': 39.265607973930074}. Best is trial 1 with value: 5.11964857237937.
[I 2024-09-07 18:40:57,187] Trial 3 finished with value: 5.144863103178045 and parameters: {'Concentration': 2.472456749209373, 'time': 23.222349340760097}. Best is trial 1 with value: 5.11964857237937.
[I 2024-09-07 18:40:57,187] Trial 4 finished with value: 5.14140341634387 a

MLR 最適解: {'Concentration': 2.999731422116364, 'time': 59.99705166610687}


In [6]:
# 結果のプロット (オプション)
fig = optuna.visualization.plot_optimization_history(study_mlr)
fig.update_layout(width=800, height=600, showlegend=False)  # 凡例を非表示に設定
show(fig)


In [7]:
# 結果のプロット (オプション)
fig = optuna.visualization.plot_contour(study_mlr)
fig.update_layout(width=800, height=600, showlegend=False)  # 凡例を非表示に設定
show(fig)


In [8]:
import numpy as np
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Input

# 目的関数の定義 (ANN 用)
def objective_ann(trial):
    # ANN モデルの定義
    model = Sequential()
    model.add(Input(shape=(2,)))  # input_dim の代わりに Input レイヤーを使用
    model.add(Dense(16, activation='relu'))
    model.add(Dense(16, activation='relu'))
    model.add(Dense(1, activation='linear'))

    # 最適化アルゴリズムと損失関数
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])

    # 試行による最適化パラメータ
    X_train = np.array([[trial.suggest_float('Concentration', 1.0, 3.0),
                         trial.suggest_float('time', 2.0, 60.0)]])
    
    # モデルのトレーニング
    model.fit(X, y_Fe, epochs=10, verbose=0)

    # 予測
    y_pred_Fe = model.predict(X_train)
    y_pred_Al = model.predict(X_train)
    y_pred_Mn = model.predict(X_train)

    # 目的関数の計算（Fe の最大化、Al の最小化、Mn の安定化）
    return -((y_pred_Fe[0][0] - y_pred_Al[0][0]) - abs(y_pred_Mn[0][0] - 5.3))


In [9]:
# Optunaによる最適化 (ANN)
study_ann = optuna.create_study(direction='minimize', sampler=TPESampler())
study_ann.optimize(objective_ann, n_trials=100)

[I 2024-09-07 18:41:22,420] A new study created in memory with name: no-name-c3eadb73-e122-46d4-9d34-5dcc523b65fc


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 56ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step


[I 2024-09-07 18:41:24,008] Trial 0 finished with value: 5.361605710536241 and parameters: {'Concentration': 1.1205844577646316, 'time': 37.07462530362207}. Best is trial 0 with value: 5.361605710536241.


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step


[I 2024-09-07 18:41:25,446] Trial 1 finished with value: 5.549337062239647 and parameters: {'Concentration': 1.4976368048452056, 'time': 41.529895510657425}. Best is trial 0 with value: 5.361605710536241.


...

[I 2024-09-07 18:44:11,133] Trial 97 finished with value: 5.402415539324283 and parameters: {'Concentration': 2.1000629577898557, 'time': 53.98726256033507}. Best is trial 10 with value: 1.632897663116455.


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 74ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step


[I 2024-09-07 18:44:12,480] Trial 98 finished with value: 5.265924493968487 and parameters: {'Concentration': 1.161991922410668, 'time': 44.566037322174836}. Best is trial 10 with value: 1.632897663116455.


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step


[I 2024-09-07 18:44:13,811] Trial 99 finished with value: 2.0077279090881346 and parameters: {'Concentration': 2.9318794049403536, 'time': 26.370662048904435}. Best is trial 10 with value: 1.632897663116455.


In [10]:
print(f"ANN 最適解: {study_ann.best_params}")

ANN 最適解: {'Concentration': 2.3076776679604682, 'time': 22.587271456539913}


In [12]:

# 結果のプロット (オプション)
fig = optuna.visualization.plot_optimization_history(study_ann)
fig.update_layout(width=800, height=600, showlegend=False)  # 凡例を非表示に設定
show(fig)


In [14]:


# 結果のプロット (オプション)
fig = optuna.visualization.plot_contour(study_ann)
fig.update_layout(width=800, height=600, showlegend=False)  # 凡例を非表示に設定
show(fig)


In [1]:
fig = optuna.visualization.plot_slice(study_ann)
fig.update_layout(width=800, height=600, showlegend=False)  # 凡例を非表示に設定
show(fig)


NameError: name 'optuna' is not defined